In [1]:
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt

C:\Users\Moon\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\Moon\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\Moon\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\Users\Moon\anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:519: FutureWarning: Passing (

In [2]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("./mnist/data/", one_hot=True)

Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting ./mnist/data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting ./mnist/data/train-labels-idx1-ubyte.gz
Instructions for updating:
Please use tf.one_hot on tensors.
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting ./mnist/data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting ./mnist/data/t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/datas

In [3]:
print(mnist.train.images)
print(mnist.train.labels)

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
[[0. 0. 0. ... 1. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 1. 0.]]


In [24]:
total_epochs = 500
batch_size = 128
learning_rate = 0.0002

In [5]:
n_hidden = 256
n_input = 28 * 28
n_noise = 128

In [6]:
X = tf.placeholder(tf.float32, [None, n_input])
Z = tf.placeholder(tf.float32, [None, n_noise])

In [7]:
G_W1 = tf.Variable(tf.random.normal([n_noise, n_hidden], stddev=0.01))
G_b1 = tf.Variable(tf.zeros([n_hidden]))
G_W2 = tf.Variable(tf.random.normal([n_hidden, n_input], stddev=0.01))
G_b2 = tf.Variable(tf.zeros([n_input]))

def generator(noise_z):
    hidden = tf.nn.relu(tf.matmul(noise_z, G_W1) + G_b1)
    output = tf.nn.sigmoid(tf.matmul(hidden, G_W2) + G_b2)
    
    return output

In [9]:
D_W1 = tf.Variable(tf.random.normal([n_input, n_hidden], stddev=0.01))
D_b1 = tf.Variable(tf.zeros([n_hidden]))
D_W2 = tf.Variable(tf.random.normal([n_hidden, 1], stddev=0.01))
D_b2 = tf.Variable(tf.zeros([1]))

def discriminator(inputs):
    hidden = tf.nn.relu(tf.matmul(inputs, D_W1) + D_b1)
    output = tf.nn.sigmoid(tf.matmul(hidden, D_W2) + D_b2)
    
    return output

In [10]:
def get_noise(batch_size, n_noise):
    return np.random.normal(size=(batch_size, n_noise))

G = generator(Z)
D_gene = discriminator(G)
D_real = discriminator(X)

In [11]:
loss_D = -tf.reduce_mean(tf.log(D_real) + tf.log(1 - D_gene))
loss_G = -tf.reduce_mean(tf.log(D_gene))

In [13]:
D_var_list = [D_W1, D_b1, D_W2, D_b2]
G_var_list = [G_W1, G_b1, G_W2, G_b2]

train_D = tf.train.AdamOptimizer(learning_rate).minimize(loss_D, var_list=D_var_list)
train_G = tf.train.AdamOptimizer(learning_rate).minimize(loss_G, var_list=G_var_list)

In [25]:
sess = tf.Session()
sess.run(tf.global_variables_initializer())

total_batch = int(mnist.train.num_examples / batch_size)
loss_val_D, loss_val_G = 0, 0

for epoch in range(total_epochs):
    for i in range(total_batch):
        batch_xs, batch_ys = mnist.train.next_batch(batch_size)
        noise = get_noise(batch_size, n_noise)
        
        _, loss_val_D = sess.run([train_D, loss_D],
                                feed_dict={X: batch_xs, Z: noise})
        _, loss_val_G = sess.run([train_G, loss_G],
                                feed_dict={Z: noise})
        
        print('Epoch: %04d, ' % (epoch + 1),
             'D loss: {:.4}, '.format(loss_val_D),
             'G loss: {:.4}'.format(loss_val_G))
        
    if epoch == 0 or (epoch + 1) % 5 == 0:
        sample_size = 10
        noise = get_noise(sample_size, n_noise)
        samples = sess.run(G, feed_dict={Z: noise})
            
        fig, ax = plt.subplots(1, sample_size, figsize=(sample_size, 1))
            
        for i in range(sample_size):
            ax[i].set_axis_off()
            ax[i].imshow(np.reshape(samples[i], (28, 28)))
                
        plt.savefig('./result/{}.png'.format(str(epoch).zfill(3)), bbox_inches='tight')
        plt.close(fig)

Epoch: 0001,  D loss: 1.387,  G loss: 0.7219
Epoch: 0001,  D loss: 1.358,  G loss: 0.7522
Epoch: 0001,  D loss: 1.332,  G loss: 0.777
Epoch: 0001,  D loss: 1.312,  G loss: 0.8004
Epoch: 0001,  D loss: 1.293,  G loss: 0.8248
Epoch: 0001,  D loss: 1.273,  G loss: 0.8499
Epoch: 0001,  D loss: 1.255,  G loss: 0.8768
Epoch: 0001,  D loss: 1.237,  G loss: 0.9039
Epoch: 0001,  D loss: 1.217,  G loss: 0.9319
Epoch: 0001,  D loss: 1.197,  G loss: 0.9617
Epoch: 0001,  D loss: 1.175,  G loss: 0.9929
Epoch: 0001,  D loss: 1.152,  G loss: 1.025
Epoch: 0001,  D loss: 1.129,  G loss: 1.058
Epoch: 0001,  D loss: 1.111,  G loss: 1.092
Epoch: 0001,  D loss: 1.085,  G loss: 1.127
Epoch: 0001,  D loss: 1.062,  G loss: 1.162
Epoch: 0001,  D loss: 1.036,  G loss: 1.198
Epoch: 0001,  D loss: 1.015,  G loss: 1.235
Epoch: 0001,  D loss: 0.9872,  G loss: 1.274
Epoch: 0001,  D loss: 0.9603,  G loss: 1.313
Epoch: 0001,  D loss: 0.9384,  G loss: 1.354
Epoch: 0001,  D loss: 0.9068,  G loss: 1.395
Epoch: 0001,  D lo

Epoch: 0001,  D loss: 0.7514,  G loss: 2.117
Epoch: 0001,  D loss: 0.7709,  G loss: 2.078
Epoch: 0001,  D loss: 0.7064,  G loss: 2.308
Epoch: 0001,  D loss: 0.7302,  G loss: 2.309
Epoch: 0001,  D loss: 0.6765,  G loss: 2.294
Epoch: 0001,  D loss: 0.7861,  G loss: 1.946
Epoch: 0001,  D loss: 0.7815,  G loss: 1.955
Epoch: 0001,  D loss: 0.7389,  G loss: 1.891
Epoch: 0001,  D loss: 0.7073,  G loss: 1.871
Epoch: 0001,  D loss: 0.7572,  G loss: 1.804
Epoch: 0001,  D loss: 0.7107,  G loss: 2.005
Epoch: 0001,  D loss: 0.7463,  G loss: 1.987
Epoch: 0001,  D loss: 0.7689,  G loss: 2.098
Epoch: 0001,  D loss: 0.7143,  G loss: 2.19
Epoch: 0001,  D loss: 0.7505,  G loss: 1.946
Epoch: 0001,  D loss: 0.7235,  G loss: 1.904
Epoch: 0001,  D loss: 0.7101,  G loss: 1.923
Epoch: 0001,  D loss: 0.7631,  G loss: 1.81
Epoch: 0001,  D loss: 0.7584,  G loss: 1.855
Epoch: 0001,  D loss: 0.7187,  G loss: 1.975
Epoch: 0001,  D loss: 0.7451,  G loss: 1.909
Epoch: 0001,  D loss: 0.7447,  G loss: 1.933
Epoch: 0001,

Epoch: 0001,  D loss: 0.6146,  G loss: 1.805
Epoch: 0001,  D loss: 0.5977,  G loss: 1.847
Epoch: 0001,  D loss: 0.6096,  G loss: 1.841
Epoch: 0001,  D loss: 0.6158,  G loss: 1.868
Epoch: 0002,  D loss: 0.6002,  G loss: 1.901
Epoch: 0002,  D loss: 0.6227,  G loss: 1.9
Epoch: 0002,  D loss: 0.6281,  G loss: 1.925
Epoch: 0002,  D loss: 0.5906,  G loss: 1.932
Epoch: 0002,  D loss: 0.5938,  G loss: 1.933
Epoch: 0002,  D loss: 0.6089,  G loss: 1.903
Epoch: 0002,  D loss: 0.6448,  G loss: 1.912
Epoch: 0002,  D loss: 0.6099,  G loss: 1.898
Epoch: 0002,  D loss: 0.6106,  G loss: 1.862
Epoch: 0002,  D loss: 0.6313,  G loss: 1.886
Epoch: 0002,  D loss: 0.5957,  G loss: 1.838
Epoch: 0002,  D loss: 0.5216,  G loss: 1.879
Epoch: 0002,  D loss: 0.629,  G loss: 1.9
Epoch: 0002,  D loss: 0.6351,  G loss: 1.901
Epoch: 0002,  D loss: 0.5513,  G loss: 1.953
Epoch: 0002,  D loss: 0.5353,  G loss: 1.983
Epoch: 0002,  D loss: 0.5599,  G loss: 1.986
Epoch: 0002,  D loss: 0.5797,  G loss: 1.991
Epoch: 0002,  D

Epoch: 0002,  D loss: 0.2619,  G loss: 2.422
Epoch: 0002,  D loss: 0.2829,  G loss: 2.441
Epoch: 0002,  D loss: 0.2475,  G loss: 2.439
Epoch: 0002,  D loss: 0.2623,  G loss: 2.465
Epoch: 0002,  D loss: 0.2746,  G loss: 2.485
Epoch: 0002,  D loss: 0.2941,  G loss: 2.493
Epoch: 0002,  D loss: 0.2748,  G loss: 2.492
Epoch: 0002,  D loss: 0.3084,  G loss: 2.48
Epoch: 0002,  D loss: 0.2755,  G loss: 2.496
Epoch: 0002,  D loss: 0.3,  G loss: 2.474
Epoch: 0002,  D loss: 0.2588,  G loss: 2.486
Epoch: 0002,  D loss: 0.2451,  G loss: 2.481
Epoch: 0002,  D loss: 0.2977,  G loss: 2.498
Epoch: 0002,  D loss: 0.257,  G loss: 2.486
Epoch: 0002,  D loss: 0.272,  G loss: 2.509
Epoch: 0002,  D loss: 0.2546,  G loss: 2.487
Epoch: 0002,  D loss: 0.2665,  G loss: 2.502
Epoch: 0002,  D loss: 0.2654,  G loss: 2.494
Epoch: 0002,  D loss: 0.2485,  G loss: 2.502
Epoch: 0002,  D loss: 0.2517,  G loss: 2.534
Epoch: 0002,  D loss: 0.2713,  G loss: 2.55
Epoch: 0002,  D loss: 0.2852,  G loss: 2.541
Epoch: 0002,  D l

Epoch: 0003,  D loss: 0.1841,  G loss: 2.789
Epoch: 0003,  D loss: 0.1946,  G loss: 2.814
Epoch: 0003,  D loss: 0.1657,  G loss: 2.818
Epoch: 0003,  D loss: 0.2024,  G loss: 2.852
Epoch: 0003,  D loss: 0.1902,  G loss: 2.851
Epoch: 0003,  D loss: 0.1795,  G loss: 2.875
Epoch: 0003,  D loss: 0.1704,  G loss: 2.872
Epoch: 0003,  D loss: 0.1994,  G loss: 2.868
Epoch: 0003,  D loss: 0.229,  G loss: 2.859
Epoch: 0003,  D loss: 0.1757,  G loss: 2.831
Epoch: 0003,  D loss: 0.1892,  G loss: 2.823
Epoch: 0003,  D loss: 0.2001,  G loss: 2.808
Epoch: 0003,  D loss: 0.1787,  G loss: 2.779
Epoch: 0003,  D loss: 0.1862,  G loss: 2.756
Epoch: 0003,  D loss: 0.1716,  G loss: 2.758
Epoch: 0003,  D loss: 0.1817,  G loss: 2.762
Epoch: 0003,  D loss: 0.206,  G loss: 2.77
Epoch: 0003,  D loss: 0.1984,  G loss: 2.775
Epoch: 0003,  D loss: 0.1537,  G loss: 2.772
Epoch: 0003,  D loss: 0.1804,  G loss: 2.817
Epoch: 0003,  D loss: 0.1798,  G loss: 2.816
Epoch: 0003,  D loss: 0.1821,  G loss: 2.833
Epoch: 0003, 

...

Epoch: 0201,  D loss: 0.4381,  G loss: 2.519
Epoch: 0201,  D loss: 0.5119,  G loss: 2.617
Epoch: 0201,  D loss: 0.4409,  G loss: 2.594
Epoch: 0201,  D loss: 0.4397,  G loss: 2.533
Epoch: 0201,  D loss: 0.4172,  G loss: 2.515
Epoch: 0201,  D loss: 0.4581,  G loss: 2.636
Epoch: 0201,  D loss: 0.5011,  G loss: 2.454
Epoch: 0201,  D loss: 0.5025,  G loss: 2.593
Epoch: 0201,  D loss: 0.5245,  G loss: 2.704
Epoch: 0201,  D loss: 0.3709,  G loss: 2.969
Epoch: 0201,  D loss: 0.4746,  G loss: 2.832
Epoch: 0201,  D loss: 0.386,  G loss: 2.953
Epoch: 0201,  D loss: 0.4987,  G loss: 2.888
Epoch: 0201,  D loss: 0.4796,  G loss: 2.788
Epoch: 0201,  D loss: 0.5726,  G loss: 2.557
Epoch: 0201,  D loss: 0.5859,  G loss: 2.247
Epoch: 0201,  D loss: 0.4428,  G loss: 2.368
Epoch: 0201,  D loss: 0.463,  G loss: 2.191
Epoch: 0201,  D loss: 0.451,  G loss: 2.449
Epoch: 0201,  D loss: 0.5075,  G loss: 2.5
Epoch: 0201,  D loss: 0.5247,  G loss: 2.423
Epoch: 0201,  D loss: 0.5713,  G loss: 2.45
Epoch: 0201,  D 

Epoch: 0202,  D loss: 0.3856,  G loss: 2.789
Epoch: 0202,  D loss: 0.5338,  G loss: 2.58
Epoch: 0202,  D loss: 0.4448,  G loss: 2.913
Epoch: 0202,  D loss: 0.4687,  G loss: 2.568
Epoch: 0202,  D loss: 0.4401,  G loss: 2.576
Epoch: 0202,  D loss: 0.5374,  G loss: 2.62
Epoch: 0202,  D loss: 0.4428,  G loss: 2.92
Epoch: 0202,  D loss: 0.5191,  G loss: 2.631
Epoch: 0202,  D loss: 0.5481,  G loss: 2.847
Epoch: 0202,  D loss: 0.488,  G loss: 2.666
Epoch: 0202,  D loss: 0.4424,  G loss: 2.767
Epoch: 0202,  D loss: 0.4906,  G loss: 2.446
Epoch: 0202,  D loss: 0.5024,  G loss: 2.635
Epoch: 0202,  D loss: 0.5064,  G loss: 2.337
Epoch: 0202,  D loss: 0.4735,  G loss: 2.4
Epoch: 0202,  D loss: 0.6269,  G loss: 2.381
Epoch: 0202,  D loss: 0.5302,  G loss: 2.458
Epoch: 0202,  D loss: 0.5451,  G loss: 2.407
Epoch: 0202,  D loss: 0.4634,  G loss: 2.374
Epoch: 0202,  D loss: 0.4543,  G loss: 2.555
Epoch: 0202,  D loss: 0.401,  G loss: 2.862
Epoch: 0202,  D loss: 0.4631,  G loss: 2.486
Epoch: 0202,  D l

Epoch: 0202,  D loss: 0.4884,  G loss: 2.647
Epoch: 0202,  D loss: 0.367,  G loss: 2.326
Epoch: 0202,  D loss: 0.5916,  G loss: 2.165
Epoch: 0202,  D loss: 0.4388,  G loss: 2.329
Epoch: 0202,  D loss: 0.4102,  G loss: 2.496
Epoch: 0202,  D loss: 0.4547,  G loss: 2.577
Epoch: 0202,  D loss: 0.5175,  G loss: 2.456
Epoch: 0202,  D loss: 0.4346,  G loss: 2.705
Epoch: 0202,  D loss: 0.4324,  G loss: 2.738
Epoch: 0202,  D loss: 0.4921,  G loss: 3.084
Epoch: 0202,  D loss: 0.4005,  G loss: 2.999
Epoch: 0202,  D loss: 0.506,  G loss: 2.663
Epoch: 0202,  D loss: 0.4177,  G loss: 2.75
Epoch: 0202,  D loss: 0.4474,  G loss: 2.599
Epoch: 0202,  D loss: 0.419,  G loss: 2.623
Epoch: 0202,  D loss: 0.4504,  G loss: 2.687
Epoch: 0202,  D loss: 0.4424,  G loss: 2.492
Epoch: 0202,  D loss: 0.4378,  G loss: 2.642
Epoch: 0202,  D loss: 0.4187,  G loss: 2.48
Epoch: 0202,  D loss: 0.4628,  G loss: 2.388
Epoch: 0202,  D loss: 0.4206,  G loss: 2.655
Epoch: 0202,  D loss: 0.483,  G loss: 2.627
Epoch: 0202,  D 

Epoch: 0203,  D loss: 0.5462,  G loss: 2.756
Epoch: 0203,  D loss: 0.3978,  G loss: 2.908
Epoch: 0203,  D loss: 0.4694,  G loss: 2.469
Epoch: 0203,  D loss: 0.4343,  G loss: 2.61
Epoch: 0203,  D loss: 0.4577,  G loss: 2.85
Epoch: 0203,  D loss: 0.5169,  G loss: 2.84
Epoch: 0203,  D loss: 0.5243,  G loss: 2.587
Epoch: 0203,  D loss: 0.4155,  G loss: 2.788
Epoch: 0203,  D loss: 0.4241,  G loss: 2.387
Epoch: 0203,  D loss: 0.4245,  G loss: 2.831
Epoch: 0203,  D loss: 0.477,  G loss: 2.427
Epoch: 0203,  D loss: 0.6237,  G loss: 2.743
Epoch: 0203,  D loss: 0.4749,  G loss: 2.872
Epoch: 0203,  D loss: 0.4169,  G loss: 2.776
Epoch: 0203,  D loss: 0.4192,  G loss: 2.674
Epoch: 0203,  D loss: 0.5063,  G loss: 2.822
Epoch: 0203,  D loss: 0.6104,  G loss: 2.868
Epoch: 0203,  D loss: 0.6173,  G loss: 2.431
Epoch: 0203,  D loss: 0.4027,  G loss: 2.755
Epoch: 0203,  D loss: 0.5234,  G loss: 2.499
Epoch: 0203,  D loss: 0.4533,  G loss: 2.558
Epoch: 0203,  D loss: 0.5108,  G loss: 2.338
Epoch: 0203,  

KeyboardInterrupt: 